# TVM Runtime base

源码见：`tvm/src/runtime/runtime_base.h`

```c++
/*!
 * \file runtime_base.h
 * \brief Base of all C APIs
 */
#ifndef TVM_RUNTIME_RUNTIME_BASE_H_
#define TVM_RUNTIME_RUNTIME_BASE_H_

#include <tvm/runtime/c_runtime_api.h>

#include <stdexcept>

/*! \brief  macro to guard beginning and end section of all functions */
#define API_BEGIN() try {
/*! \brief every function starts with API_BEGIN();
     and finishes with API_END() or API_END_HANDLE_ERROR */
#define API_END()                                         \
  }                                                       \
  catch (::tvm::runtime::EnvErrorAlreadySet & _except_) { \
    return -2;                                            \
  }                                                       \
  catch (std::exception & _except_) {                     \
    return TVMAPIHandleException(_except_);               \
  }                                                       \
  return 0;  // NOLINT(*)
/*!
 * \brief every function starts with API_BEGIN();
 *   and finishes with API_END() or API_END_HANDLE_ERROR
 *   The finally clause contains procedure to cleanup states when an error happens.
 */
#define API_END_HANDLE_ERROR(Finalize)                    \
  }                                                       \
  catch (::tvm::runtime::EnvErrorAlreadySet & _except_) { \
    return -2;                                            \
  }                                                       \
  catch (std::exception & _except_) {                     \
    Finalize;                                             \
    return TVMAPIHandleException(_except_);               \
  }                                                       \
  return 0;  // NOLINT(*)

/*!
 * \brief handle exception throwed out
 * \param e the exception
 * \return the return value of API after exception is handled
 */
int TVMAPIHandleException(const std::exception& e);

#endif  // TVM_RUNTIME_RUNTIME_BASE_H_
```

这段代码是 C++ 头文件，它定义了一些宏和函数，用于处理 TVM 运行时 API 的异常情况。

首先，该头文件包含了一些必要的头文件：

- `<tvm/runtime/c_runtime_api.h>`：包含 TVM C API 的声明。
- `<stdexcept>`：包含标准异常类的定义。

接下来，定义了两个宏：
1. `API_BEGIN()`：用于标记函数开始执行的位置。在函数体中，使用 `try` 块来捕获可能抛出的异常。
2. `API_END()`：用于标记函数结束执行的位置。在函数体中，使用 `catch` 块来捕获特定的异常类型，并返回相应的错误码。如果没有捕获到任何异常，则返回 `0` 表示成功。如果发生了 `EnvErrorAlreadySet` 异常，则返回 `-2`；如果发生了其他类型的异常，则调用  `TVMAPIHandleException()` 函数来处理异常并返回相应的值。

此外，还定义了宏 `API_END_HANDLE_ERROR(Finalize)`，用于处理异常并在发生错误时执行清理操作。与 `API_END()` 类似，它也使用 `try` 和 `catch` 块来捕获异常，但在捕获到异常后，会先执行传入的 `Finalize` 参数所表示的清理操作，然后再调用 `TVMAPIHandleException()` 函数处理异常并返回相应的错误码。

最后，定义了函数 `TVMAPIHandleException()`，用于处理异常。它接受 `std::exception` 类型的参数，并返回整数值，表示 API 执行后的返回值。